In [1]:
!pip install -U pyabsa

  Using cached transformers-4.51.3-py3-none-any.whl.metadata (38 kB)
Using cached transformers-4.51.3-py3-none-any.whl (10.4 MB)


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModel, AutoConfig
import torch.nn as nn
import os
from typing import Dict, Optional, Union, List

class ABSARegressor(nn.Module):
    """
    BERT-based regression model for aspect-based sentiment analysis
    """
    def __init__(
        self,
        base_model_name: str = "GiRak/beer-sentiment-bert",
        dropout_rate: float = 0.1,
        freeze_encoder: bool = True
    ):
        super().__init__()
        config = AutoConfig.from_pretrained(base_model_name)
        self.bert = AutoModel.from_pretrained(base_model_name, config=config)
        if freeze_encoder:
            for param in self.bert.parameters():
                param.requires_grad = False
        self.dropout = nn.Dropout(dropout_rate)
        hidden_size = config.hidden_size
        self.regressor = nn.Linear(hidden_size, 1)

    def forward(self, input_ids, attention_mask, labels=None):
        bert_outputs = self.bert(
            input_ids=input_ids,
            attention_mask=attention_mask
        )
        pooled = bert_outputs.pooler_output
        x = self.dropout(pooled)
        logits = self.regressor(x).squeeze(-1)
        output = {"logits": logits}
        if labels is not None:
            loss_fct = nn.MSELoss()
            output["loss"] = loss_fct(logits, labels)
        return output

class BeerReviewAnalyzer:
    """
    啤酒评论分析器类，封装了模型加载和预测功能
    """
    def __init__(
        self,
        model_path: str = "1-sentiment-analysis/models/absa_bert_regressor",
        base_model_name: str = "GiRak/beer-sentiment-bert",
        device: str = "cuda" if torch.cuda.is_available() else "cpu"
    ):
        """
        初始化分析器
        
        Args:
            model_path: 模型路径
            base_model_name: 基础BERT模型名称
            device: 运行设备 ('cuda' 或 'cpu')
        """
        self.device = device
        self.model_path = model_path
        self.base_model_name = base_model_name
        self.aspects = ["look", "smell", "taste", "feel"]
        
        # 加载模型和分词器
        self._load_model_and_tokenizer()
        
    def _load_model_and_tokenizer(self):
        """加载模型和分词器"""
        try:
            # 加载分词器
            self.tokenizer = AutoTokenizer.from_pretrained(self.base_model_name)
            print("Tokenizer loaded successfully!")

            # 检查模型路径
            if not os.path.exists(self.model_path):
                print(f"Warning: Model path {self.model_path} does not exist")
                alt_path = "../1-sentiment-analysis/models/absa_bert_regressor"
                if os.path.exists(alt_path):
                    self.model_path = alt_path
                else:
                    raise FileNotFoundError(f"Model not found in {self.model_path} or {alt_path}")

            print(f"Loading model from: {self.model_path}")

            # 初始化模型
            self.model = ABSARegressor()
            
            # 加载模型权重
            state_dict = torch.load(
                os.path.join(self.model_path, "model.safetensors"),
                map_location=torch.device(self.device),
                weights_only=False
            )
            self.model.load_state_dict(state_dict)
            self.model.to(self.device)
            self.model.eval()
            print("Model loaded successfully!")
            
        except Exception as e:
            print(f"Error loading model: {str(e)}")
            raise

    def analyze_review(
        self,
        text: str,
        aspects: Optional[List[str]] = None,
        return_dict: bool = True
    ) -> Union[Dict[str, float], List[float]]:
        """
        分析啤酒评论
        
        Args:
            text: 评论文本
            aspects: 要分析的具体方面，如果为None则分析所有方面
            return_dict: 是否返回字典格式的结果
            
        Returns:
            如果 return_dict=True，返回 {aspect: score} 格式的字典
            如果 return_dict=False，返回 [score1, score2, ...] 格式的列表
        """
        if aspects is None:
            aspects = self.aspects
            
        try:
            results = {}
            with torch.no_grad():
                for aspect in aspects:
                    input_text = f"{aspect}: {text}"
                    inputs = self.tokenizer(
                        input_text,
                        truncation=True,
                        padding="max_length",
                        max_length=128,
                        return_tensors="pt"
                    ).to(self.device)
                    
                    outputs = self.model(**inputs)
                    score = outputs["logits"].item()
                    results[aspect] = round(score, 2)
            
            return results if return_dict else list(results.values())
            
        except Exception as e:
            print(f"Error during prediction: {str(e)}")
            return None

    def analyze_batch(
        self,
        texts: List[str],
        aspects: Optional[List[str]] = None
    ) -> List[Dict[str, float]]:
        """
        批量分析多个评论
        
        Args:
            texts: 评论文本列表
            aspects: 要分析的具体方面
            
        Returns:
            包含每个评论分析结果的列表
        """
        return [self.analyze_review(text, aspects) for text in texts]

    def get_model_info(self) -> Dict:
        """
        获取模型信息
        
        Returns:
            包含模型信息的字典
        """
        return {
            "device": self.device,
            "model_path": self.model_path,
            "base_model": self.base_model_name,
            "num_parameters": sum(p.numel() for p in self.model.parameters()),
            "vocab_size": len(self.tokenizer),
            "aspects": self.aspects
        }

# 使用示例
if __name__ == "__main__":
    # 初始化分析器
    analyzer = BeerReviewAnalyzer()
    
    # 分析单个评论
    review = "This beer has a beautiful golden color with a nice head. The aroma is fruity and hoppy. The taste is well-balanced with a slight bitterness. The mouthfeel is smooth and creamy."
    results = analyzer.analyze_review(review)
    print("\nSingle review analysis:")
    for aspect, score in results.items():
        print(f"{aspect}: {score}")
    
    # 批量分析多个评论
    reviews = [
        "The beer looks cloudy and dark. It smells like coffee and chocolate. The taste is very bitter and strong. The mouthfeel is thick and heavy.",
        "Clear golden color with a white head. Aroma of citrus and pine. Taste is balanced with a nice hop bitterness. Smooth mouthfeel."
    ]
    batch_results = analyzer.analyze_batch(reviews)
    print("\nBatch analysis results:")
    for i, result in enumerate(batch_results, 1):
        print(f"\nReview {i}:")
        for aspect, score in result.items():
            print(f"{aspect}: {score}")
    
    # 获取模型信息
    model_info = analyzer.get_model_info()
    print("\nModel Information:")
    for key, value in model_info.items():
        print(f"{key}: {value}")

Tokenizer loaded successfully!
Loading model from: ../1-sentiment-analysis/models/absa_bert_regressor
Error loading model: invalid load key, '\xe0'.


UnpicklingError: invalid load key, '\xe0'.

In [2]:
!pip show pyabsa

Name: pyabsa
Version: 2.4.1.post1
Summary: This tool provides the state-of-the-art models for aspect term extraction (ATE), aspect polarity classification (APC), and text classification (TC).
Home-page: https://github.com/yangheng95/PyABSA
Author: Yang, Heng
Author-email: hy345@exeter.ac.uk
License: MIT
Location: /opt/homebrew/anaconda3/envs/pytorch/lib/python3.12/site-packages
Requires: autocuda, boostaug, findfile, gitpython, metric-visualizer, networkx, pandas, protobuf, pytorch-warmup, sentencepiece, seqeval, spacy, termcolor, torch, tqdm, transformers, typing-extensions, update-checker
Required-by: boostaug


In [ ]:
# !pip uninstall transformers -y
# !pip install transformers==4.29.2

Found existing installation: transformers 4.51.3
Uninstalling transformers-4.51.3:
  Successfully uninstalled transformers-4.51.3
  Using cached transformers-4.29.2-py3-none-any.whl.metadata (112 kB)
  Using cached tokenizers-0.13.3.tar.gz (314 kB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
Using cached transformers-4.29.2-py3-none-any.whl (7.1 MB)
  error: subprocess-exited-with-error
  
  × Building wheel for tokenizers (pyproject.toml) did not run successfully.
  │ exit code: 1
  ╰─> [62 lines of output]
      /private/var/folders/fh/_tq_jbr50895yx1hkbgpct5m0000gn/T/pip-build-env-id4j44nr/overlay/lib/python3.12/site-packages/setuptools/dist.py:759: SetuptoolsDeprecationWarning: License classifiers are deprecated.
      !!
      
              ********************************************************************************
              Please consider removing the following classifiers in fav

In [6]:
import pandas as pd
import re
import emoji
from langdetect import detect
from pyabsa import AspectPolarityClassification as APC
import dask.dataframe as dd
import dask
from tqdm import tqdm

No CUDA GPU found in your device


/bin/sh: nvidia-smi: command not found


[2025-05-02 00:21:42] (2.4.1.post1) PyABSA(2.4.1.post1): If your code crashes on Colab, please use the GPU runtime. Then run "pip install pyabsa[dev] -U" and restart the kernel.
Or if it does not work, you can use v1.x versions, e.g., pip install pyabsa<2.0 -U




Try to downgrade transformers<=4.29.0.






/opt/homebrew/anaconda3/envs/pytorch/lib/python3.12/multiprocessing/pool.py:268: ResourceWarning: unclosed running multiprocessing pool <multiprocessing.pool.Pool state=RUN pool_size=1>
  _warn(f"unclosed running multiprocessing pool {self!r}",


In [36]:
csv_path = '../data/reviews_stratified_sampled.csv'
# Load the CSV file with Dask (lazy evaluation)
df = pd.read_csv(csv_path)

In [37]:
df

beer_id          username        date  \
0         1428           Aethien  2012-02-12   
1         4351        kojevergas  2011-07-31   
2        70485           CMUbrew  2012-03-10   
3        27069         maximum12  2010-05-12   
4        44788       HarleyRider  2010-06-26   
...        ...               ...         ...   
27697    90141  BlackBelt5112203  2013-07-26   
27698     2128     woodychandler  2011-08-08   
27699    19216          05Harley  2011-02-25   
27700    41951   brewdlyhooked13  2008-07-19   
27701    98387         superspak  2014-02-12   

                                                    text  look  smell  taste  \
0         poured into a tulip, it looks a nice golden...  3.00    1.5    1.5   
1         can served into norrebro bryghus stemware i...  2.50    2.0    2.0   
2         reviewed from notes 500ml can poured into a...  3.00    1.0    1.0   
3         rec'd a bottle of this unbidden in a recent...  2.50    2.0    2.0   
4         heading out on the boat my wife brings home...  3.00    1.0    1.0   
...                                                  ...   ...    ...    ...   
27697     5 oz pour into a tasting glass on tap at th...  4.25    4.5    4.5   
27698     an afternoon of aus beers continued at my a...  4.00    4.0    4.0   
27699     bottled on: (should be on the bottom right ...  5.00    4.0    4.0   
27700     appearance - pours a dark reddish caramel w...  4.00    4.0    4.0   
27701     22 ounce bottle into tulip glass, bottled o...  4.00    4.5    4.0   

       feel  overall  score  has_look  has_smell  has_taste  has_feel  \
0       2.0      2.0   1.74      True       True       True      True   
1       1.5      2.0   1.98      True       True       True      True   
2       1.5      1.0   1.17      True       True       True      True   
3       2.0      1.0   1.83      True       True       True      True   
4       3.0      2.0   1.52      True       True       True      True   
...     ...      ...    ...       ...        ...        ...       ...   
27697   4.0      4.5   4.44      True       True       True      True   
27698   4.0      4.0   4.00      True       True       True      True   
27699   4.0      4.0   4.06      True       True       True      True   
27700   4.5      5.0   4.25      True       True       True      True   
27701   4.0      4.5   4.22      True       True       True      True   

              mentioned_aspects sentiment  
0      look, smell, taste, feel  negative  
1      look, smell, taste, feel  negative  
2      look, smell, taste, feel  negative  
3      look, smell, taste, feel  negative  
4      look, smell, taste, feel  negative  
...                         ...       ...  
27697  look, smell, taste, feel  positive  
27698  look, smell, taste, feel  positive  
27699  look, smell, taste, feel  positive  
27700  look, smell, taste, feel  positive  
27701  look, smell, taste, feel  positive  

[27702 rows x 16 columns]

In [38]:
## 2. Preprocessing for the Aspect Polarity Classification
import re
import emoji

def clean_text(text):
    text = str(text)
    text = re.sub(r'<.*?>', '', text)                       # Remove HTML
    text = re.sub(r'http\S+|www\.\S+', '', text)            # Remove URLs
    text = re.sub(r'\S+@\S+', '', text)                     # Remove emails
    text = emoji.demojize(text)                             # Convert emojis to :heart:, etc.
    return text.strip()
    
df['text'] = df['text'].apply(clean_text)

In [39]:
# Step 2: Sample a larger set for processing (e.g. 1000 rows)
df_sample = df.sample(n=1000, random_state=42).copy()

# Step 3: Load the pre-trained sentiment classifier
classifier = APC.SentimentClassifier(checkpoint='english')

# Step 4: Define target aspects
aspects = ['look', 'smell', 'taste', 'feel']

# Step 5: Extract aspect-level sentiments
for aspect in aspects:
    print(f"\nProcessing aspect: {aspect}")
    sentiments = []
    for text in tqdm(df_sample['text']):
        try:
            result = classifier.predict(text=text, aspect=aspect)
            sentiments.append(result['sentiment'])
        except Exception as e:
            sentiments.append('unknown')  # fallback in case of error
    df_sample[f'{aspect}_sentiment'] = sentiments

# Step 6: Save results to new CSV
output_path = '../data/reviews_with_aspect_sentiment_test.csv'
df_sample.to_csv(output_path, index=False)
print(f"\n Saved to: {output_path}")

[2025-05-02 14:43:04] (2.4.1.post1) ********** Available APC model checkpoints for Version:2.4.1.post1 (this version) **********
[2025-05-02 14:43:04] (2.4.1.post1) ********** Available APC model checkpoints for Version:2.4.1.post1 (this version) **********
[2025-05-02 14:43:04] (2.4.1.post1) Downloading checkpoint:english 
[2025-05-02 14:43:04] (2.4.1.post1) Notice: The pretrained model are used for testing, it is recommended to train the model on your own custom datasets
[2025-05-02 14:43:04] (2.4.1.post1) Checkpoint already downloaded, skip
[2025-05-02 14:43:04] (2.4.1.post1) Load sentiment classifier from checkpoints/APC_ENGLISH_CHECKPOINT/fast_lsa_t_v2_English_acc_82.21_f1_81.81
[2025-05-02 14:43:04] (2.4.1.post1) config: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lsa_t_v2_English_acc_82.21_f1_81.81/fast_lsa_t_v2.config
[2025-05-02 14:43:04] (2.4.1.post1) state_dict: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lsa_t_v2_English_acc_82.21_f1_81.81/fast_lsa_t_v2.state_dict
[2025-05-02 14:43

/opt/homebrew/anaconda3/envs/pytorch/lib/python3.12/site-packages/transformers/convert_slow_tokenizer.py:559: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(



Processing aspect: look


  0%|          | 0/1000 [00:00<?, ?it/s]

[2025-05-02 14:44:08] (2.4.1.post1) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] 12 oz bottle pours a mostly clear, golden color with a miniscule wisp of white head, even with a fairly aggressive pour. nose is more malty than hoppy with light caramel and grains leading the way. no matter how hard i try, i cant pick out any hops...fail. taste is caramel malt, touch of butterscotch...and still no damn hops. this is weak sauce indeed. amber ale, maybe...pale ale, meh, thats pushing it...ipa? hellz to the no. label says established in 2012...if they are not careful, they will be extinct by 2013. mouthfeel is tannic, husky and undercarbonated. basically this beer sucks, one of the worst beers from the lone star state, and thats saying something!
[2025-05-02 14:44:08] (2.4.1.post1) Example 0: 12 oz bottle pours a mostly clear, golden color with a miniscule wisp of white head, even with a fairly aggressive p

...

[2025-05-02 14:58:32] (2.4.1.post1) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] this is the second of three subjects in the high-low invitation. bud ice light is out of the way, and in come a new kind of beer i will try tonight: non-alcoholic beer. labeled as a "malt beverage with natural flavors". sounds like something you'd see on a malternative. anyway, on to the....um...beverage: i regret this now, but i poured this beverage into a glass, and got a soda-like fizzy head with a scary body. very clean smell, mainly because there's almost nothing to detect. the taste could use some better balance, but maybe that's the character of a na (remember, this is my first na brew). i could only get a weird syrup sweetness out of it. whatever else is in there could be smoothed out. bud ice light beats out coors na in this round, but must take on olde english malt liquor to win the crown for the high-low invita

100%|█████████▉| 999/1000 [03:49<00:00,  3.47it/s]

[2025-05-02 14:58:32] (2.4.1.post1) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] thanks to daniel for this bottle. this one pours black with a rapidly growing mocha head, tall, thick, recedes at a moderate pace leaving lots of lace. aroma has a worty barley scent along with roast and a touch of honey sweetness. good balance between roast and sweet on the nose. flavor has coffee, but not nearly as sharp of a roast as other dry stouts i have tried, smooth and semisweet initially, then a pleasant roasted barley bitterness and cookie finish. nicely done, the roasted malt avoids acrid sensation for a refreshing beer. somewhat insubstantial body, but expected for the style, moderate to heavier carbonation is expected, maybe a bit much on the bubbles though. drinkability is definitely high, not many beers of this strength are as easily quaffable.
[2025-05-02 14:58:32] (2.4.1.post1) Example 0: thanks to danie

100%|██████████| 1000/1000 [03:49<00:00,  4.35it/s]



 Saved to: ../data/reviews_with_aspect_sentiment_test.csv


In [27]:
# Load the output file with aspect-level sentiment columns
df_result = pd.read_csv('../data/reviews_with_aspect_sentiment_test.csv')

In [28]:
# Show the first 10 rows
df_result.head(10)

beer_id         username        date  \
0    86061  twiggamortis420  2012-11-03   
1     3435           Viking  2002-10-12   
2    18862          ElGallo  2011-02-17   
3      114       TastyTaste  2006-03-28   
4    63022      BeerNemesis  2011-05-16   
5    34420            Phatz  2007-02-25   
6    88422           garuda  2013-01-20   
7      837  KYFriedChildren  2010-09-17   
8     5832    francisweizen  2005-07-19   
9    87134         thain709  2013-02-18   

                                                text  look  smell  taste  \
0     12 oz bottle pours a mostly clear, golden c...  2.50    2.0    1.5   
1     i wish i had read these reviews before i op...  4.00    4.5    4.0   
2     12-oz. bottle poured into a balloon snifter...  4.00    4.0    4.0   
3     appearance: fills up about 2/3 of my goblet...  3.50    4.0    4.0   
4     0% anchor christmas ale | 330 ml. | 5.5% ab...  4.00    4.0    4.0   
5     it was a real pleasure to meet ba johnmicha...  4.50    5.0    5.0   
6     a - nearly black, off-white head has good r...  3.75    2.5    3.5   
7     poured one of my old man's brews into a pin...  1.50    1.0    1.5   
8     vintage 750ml botte. interesting. a golden ...  4.00    4.0    4.0   
9     a - pours with an almost black body...there...  3.75    4.0    4.0   

   feel  overall  score  has_look  has_smell  has_taste  has_feel  \
0  1.50     2.00   1.78      True       True       True      True   
1  4.00     4.00   4.12      True       True       True      True   
2  4.00     4.50   4.10      True       True       True      True   
3  4.50     4.50   4.12      True       True       True      True   
4  3.00     4.00   3.90      True       True       True      True   
5  4.50     4.50   4.82      True       True       True      True   
6  3.75     3.50   3.30      True       True       True      True   
7  1.50     2.00   1.48      True       True       True      True   
8  4.00     4.00   4.00      True       True       True      True   
9  3.75     3.75   3.91      True       True       True      True   

          mentioned_aspects sentiment look_sentiment smell_sentiment  \
0  look, smell, taste, feel  negative   ['Positive']    ['Positive']   
1  look, smell, taste, feel  positive    ['Neutral']     ['Neutral']   
2  look, smell, taste, feel  positive   ['Positive']    ['Positive']   
3  look, smell, taste, feel  positive   ['Positive']    ['Positive']   
4  look, smell, taste, feel   neutral    ['Neutral']     ['Neutral']   
5  look, smell, taste, feel  positive   ['Positive']    ['Positive']   
6  look, smell, taste, feel   neutral    ['Neutral']     ['Neutral']   
7  look, smell, taste, feel  negative   ['Negative']    ['Negative']   
8  look, smell, taste, feel  positive   ['Positive']    ['Positive']   
9  look, smell, taste, feel   neutral   ['Positive']    ['Positive']   

  taste_sentiment feel_sentiment  
0    ['Positive']   ['Positive']  
1     ['Neutral']    ['Neutral']  
2    ['Positive']   ['Positive']  
3    ['Positive']   ['Positive']  
4     ['Neutral']    ['Neutral']  
5    ['Positive']   ['Positive']  
6     ['Neutral']    ['Neutral']  
7    ['Negative']   ['Negative']  
8    ['Positive']   ['Positive']  
9    ['Positive']   ['Positive']

In [29]:
for col in ['look_sentiment', 'smell_sentiment', 'taste_sentiment', 'feel_sentiment']:
    df_result[col] = df_result[col].apply(lambda x: eval(x)[0] if isinstance(x, str) else x)
    df_result[col] = df_result[col].str.lower()

df_result['sentiment'] = df_result['sentiment'].str.lower()

In [31]:
def aggregate_aspect_sentiment(row):
    aspects = [row['look_sentiment'], row['smell_sentiment'], row['taste_sentiment'], row['feel_sentiment']]
    pos = aspects.count('positive')
    neg = aspects.count('negative')
    if pos >= 2:
        return 'positive'
    elif neg >= 2:
        return 'negative'
    else:
        return 'neutral'

df_result['aggregated_aspect_sentiment'] = df_result.apply(aggregate_aspect_sentiment, axis=1)

In [34]:
df_result['match'] = df_result['sentiment'] == df_result['aggregated_aspect_sentiment']
accuracy = df_result['match'].mean()
print(f"Consistency between labeled sentiment and aspect-derived sentiment: {accuracy:.2%}")

Consistency between labeled sentiment and aspect-derived sentiment: 49.00%


In [35]:
df_result

beer_id         username        date  \
0     86061  twiggamortis420  2012-11-03   
1      3435           Viking  2002-10-12   
2     18862          ElGallo  2011-02-17   
3       114       TastyTaste  2006-03-28   
4     63022      BeerNemesis  2011-05-16   
..      ...              ...         ...   
95     3734           smcolw  2008-01-20   
96     9086          BARFLYB  2009-01-04   
97   226383    woodychandler  2016-07-21   
98    30420        jonziefle  2009-04-24   
99    58714         Pencible  2010-07-20   

                                                 text  look  smell  taste  \
0      12 oz bottle pours a mostly clear, golden c...   2.5   2.00    1.5   
1      i wish i had read these reviews before i op...   4.0   4.50    4.0   
2      12-oz. bottle poured into a balloon snifter...   4.0   4.00    4.0   
3      appearance: fills up about 2/3 of my goblet...   3.5   4.00    4.0   
4      0% anchor christmas ale | 330 ml. | 5.5% ab...   4.0   4.00    4.0   
..                                                ...   ...    ...    ...   
95     this beer pours a straw yellow color and is...   4.0   1.50    1.0   
96     12oz bottle poured into dogfish head pint g...   3.0   3.50    4.0   
97     i picked this up recently at the fridge and...   4.0   4.25    3.5   
98     appearance: poured a clear amber, with a hi...   4.5   4.00    3.5   
99     a: this poured clear copper with moderate l...   4.0   3.00    3.0   

    feel  overall  score  ...  has_taste  has_feel         mentioned_aspects  \
0   1.50      2.0   1.78  ...       True      True  look, smell, taste, feel   
1   4.00      4.0   4.12  ...       True      True  look, smell, taste, feel   
2   4.00      4.5   4.10  ...       True      True  look, smell, taste, feel   
3   4.50      4.5   4.12  ...       True      True  look, smell, taste, feel   
4   3.00      4.0   3.90  ...       True      True  look, smell, taste, feel   
..   ...      ...    ...  ...        ...       ...                       ...   
95  1.00      1.0   1.30  ...       True      True  look, smell, taste, feel   
96  3.50      3.0   3.57  ...       True      True  look, smell, taste, feel   
97  3.75      4.0   3.84  ...       True      True  look, smell, taste, feel   
98  3.50      3.5   3.68  ...       True      True  look, smell, taste, feel   
99  4.50      3.0   3.21  ...       True      True  look, smell, taste, feel   

    sentiment look_sentiment smell_sentiment taste_sentiment feel_sentiment  \
0    negative       positive        positive        positive       positive   
1    positive        neutral         neutral         neutral        neutral   
2    positive       positive        positive        positive       positive   
3    positive       positive        positive        positive       positive   
4     neutral        neutral         neutral         neutral        neutral   
..        ...            ...             ...             ...            ...   
95   negative       positive        positive        positive       positive   
96    neutral       positive        positive        positive       positive   
97    neutral       positive        positive        positive       positive   
98    neutral       positive        positive        positive       positive   
99    neutral       positive        positive        positive       positive   

   aggregated_aspect_sentiment  match  
0                     positive  False  
1                      neutral  False  
2                     positive   True  
3                     positive   True  
4                      neutral   True  
..                         ...    ...  
95                    positive  False  
96                    positive  False  
97                    positive  False  
98                    positive  False  
99                    positive  False  

[100 rows x 22 columns]